# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.
mongoimport --db=uk_food --collection=establishments --file="C:\Users\steph\UofM-VIRT-DATA-PT-12-2024-U-LOLC-MWTH\02-Homework\12-NoSQL-Databases\Starter_Code\Resources\establishments.json" --jsonArray


In [54]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [55]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [56]:
# confirm that our new database was created
mongo.list_database_names()

['admin', 'config', 'local', 'uk_food']

In [57]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [92]:
# review the collections in our new database
db.list_collection_names()

['establishments']

In [93]:
# review a document in the establishments collection
db.establishments.find_one()

{'_id': ObjectId('67d32cca31ad51a27e209c07'),
 'FHRSID': 1034540,
 'ChangesByServerID': 0,
 'LocalAuthorityBusinessID': 'PI/000078691',
 'BusinessName': 'The Coastguard Inn',
 'BusinessType': 'Pub/bar/nightclub',
 'BusinessTypeID': 7843,
 'AddressLine1': 'The Bay',
 'AddressLine2': 'St Margarets Bay',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'PostCode': 'CT15 6DY',
 'Phone': '',
 'RatingValue': '5',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingDate': '2022-08-17T00:00:00',
 'LocalAuthorityCode': '182',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'scores': {'Hygiene': 0, 'Structural': 5, 'ConfidenceInManagement': 0},
 'SchemeType': 'FHRS',
 'geocode': {'longitude': '1.387974', 'latitude': '51.152225'},
 'RightToReply': '',
 'Distance': 4587.347174863443,
 'NewRatingPending': False,
 'meta': {'dataSource': None,
  'extractDate': '0001-01-01T00:00:00',
  'itemCount': 0,
  'returncode'

In [94]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [95]:
# Create a dictionary for the new restaurant data
new_doc={
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [96]:
# Insert the new restaurant into the collection
establishments.insert_one(new_doc)

InsertOneResult(ObjectId('67d32cea95e661ecd8d3ea76'), acknowledged=True)

In [97]:
# Check that the new restaurant was inserted
r=establishments.find({'BusinessName':"Penang Flavours"})
for i in r:
    print(i)

{'_id': ObjectId('67d32cea95e661ecd8d3ea76'), 'BusinessName': 'Penang Flavours', 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': '', 'AddressLine1': 'Penang Flavours', 'AddressLine2': '146A Plumstead Rd', 'AddressLine3': 'London', 'AddressLine4': '', 'PostCode': 'SE18 7DY', 'Phone': '', 'LocalAuthorityCode': '511', 'LocalAuthorityName': 'Greenwich', 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk', 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk', 'scores': {'Hygiene': '', 'Structural': '', 'ConfidenceInManagement': ''}, 'SchemeType': 'FHRS', 'geocode': {'longitude': '0.08384000', 'latitude': '51.49014200'}, 'RightToReply': '', 'Distance': 4623.972328074718, 'NewRatingPending': True}


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [98]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields

d=establishments.find_one({'BusinessType':"Restaurant/Cafe/Canteen"},{'BusinessTypeID':1,'BusinessType':1})
print(d)
canteen_id=d['BusinessTypeID']

{'_id': ObjectId('67d32cca31ad51a27e209c08'), 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [99]:
# Update the new restaurant with the correct BusinessTypeID
establishments.update_one({'BusinessName':"Penang Flavours"},{'$set':{'BusinessTypeID':canteen_id}})

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [100]:
# Confirm that the new restaurant was updated

for doc in establishments.find({'BusinessName':"Penang Flavours"},{'BusinessTypeID':1}):
    print(doc)

{'_id': ObjectId('67d32cea95e661ecd8d3ea76'), 'BusinessTypeID': 1}


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [101]:
# Find how many documents have LocalAuthorityName as "Dover"
establishments.count_documents({'LocalAuthorityName':'Dover'})

994

In [102]:
# Delete all documents where LocalAuthorityName is "Dover"
establishments.delete_many({'LocalAuthorityName':'Dover'})

DeleteResult({'n': 994, 'ok': 1.0}, acknowledged=True)

In [104]:
# Check if any remaining documents include Dover
establishments.count_documents({'LocalAuthorityName':'Dover'})

0

In [103]:
# Check that other documents remain with 'find_one'
establishments.find_one()

{'_id': ObjectId('67d32cca31ad51a27e209eed'),
 'FHRSID': 289353,
 'ChangesByServerID': 0,
 'LocalAuthorityBusinessID': 'PI/000002468',
 'BusinessName': 'St Marys COE (aided) Primary School',
 'BusinessType': 'School/college/university',
 'BusinessTypeID': 7845,
 'AddressLine1': 'St Marys Church Of England Primary School',
 'AddressLine2': 'Warren Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'PostCode': 'CT19 6QH',
 'Phone': '',
 'RatingValue': '5',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingDate': '2016-09-13T00:00:00',
 'LocalAuthorityCode': '188',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'scores': {'Hygiene': 0, 'Structural': 0, 'ConfidenceInManagement': 0},
 'SchemeType': 'FHRS',
 'geocode': {'longitude': '1.194762', 'latitude': '51.085797'},
 'RightToReply': '',
 'Distance': 4591.871474174837,
 'NewRatingPending': False,
 'meta': {'

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [105]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many({},[{'$set':{'geocode.latitude':{'$toDecimal':'$geocode.latitude'},'geocode.longitude':{'$toDecimal':'$geocode.longitude'}}}])

UpdateResult({'n': 38786, 'nModified': 38786, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

Use `update_many` to convert `RatingValue` to integer numbers.

In [106]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 4091, 'nModified': 4091, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [107]:
# Change the data type from String to Integer for RatingValue
establishments.update_many({},[{'$set':{'RatingValue':{'$toInt':'$RatingValue'}}}])

UpdateResult({'n': 38786, 'nModified': 34695, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [110]:
# Check that the coordinates and rating value are now numbers
for doc in establishments.find({},{'geocode.latitude':1,'geocode.longitude':1,'RatingValue':1}):
    pprint(doc)

{'RatingValue': 5,
 '_id': ObjectId('67d32cca31ad51a27e209eed'),
 'geocode': {'latitude': Decimal128('51.085797'),
             'longitude': Decimal128('1.194762')}}
{'RatingValue': 4,
 '_id': ObjectId('67d32cca31ad51a27e209eef'),
 'geocode': {'latitude': Decimal128('51.086058'),
             'longitude': Decimal128('1.196408')}}
{'RatingValue': 5,
 '_id': ObjectId('67d32cca31ad51a27e209ef0'),
 'geocode': {'latitude': Decimal128('51.083812'),
             'longitude': Decimal128('1.195625')}}
{'RatingValue': 4,
 '_id': ObjectId('67d32cca31ad51a27e209ef3'),
 'geocode': {'latitude': Decimal128('51.08084'),
             'longitude': Decimal128('1.188537')}}
{'RatingValue': 5,
 '_id': ObjectId('67d32cca31ad51a27e209ef4'),
 'geocode': {'latitude': Decimal128('51.08084'),
             'longitude': Decimal128('1.188537')}}
{'RatingValue': 5,
 '_id': ObjectId('67d32cca31ad51a27e209ef5'),
 'geocode': {'latitude': Decimal128('51.08084'),
             'longitude': Decimal128('1.188537')}}
{'Ratin